# Probabilistic classification algorithms

In this tutorial we will implement a Naive Bayes classifier for text classification. More specifically, the aim of the classifier is to predict whether a given product review is positive or negative.

We will represent documents (i.e. product reviews) as vectors of binary features. For each [unigram or bigram](https://en.wikipedia.org/wiki/N-gram) that appears in at least one document in our training dataset we introduce a binary feature. For a given document a feature is 1 if the documents contains the corresponding unigram/bigram, and it is 0 otherwise.

The datasets are contained in four files ('test.negative', 'test.positive', 'train.negative', 'train.positive'). The files correspond to product reviews from the test and train datasets labelled positively or negatively. For example, the file 'test.negative' contains negative product reviews from the test dataset.

The reviews are preprocessed and expressed as a list of unigrams and bigrams without duplications (for a bigram (w1,w2), the corresponding record is w1__w2). Each review is represented as a single line and features (unigrams and bigrams) extracted from that review are listed space delimited. Take a moment to inspect the content of the dataset files.

In [2]:
import numpy as np

1. First, we read the training data, compute feature statistics, and store it in a [dictionary](https://docs.python.org/3/tutorial/datastructures.html#dictionaries) $\texttt{featureStat}$, where $\texttt{featureStat[feature][classLabel]}$ is equal to the number of documents in the class $\texttt{classLabel}$ that contain $\texttt{feature}$. We also compute the total number of positive train instances and the total number of negative train instances.

In [3]:
def count(featureStat, fname, classLabel):
    numInstances = 0
    with open(fname) as file:
        for line in file:
            numInstances += 1
            for feature in line.strip().split():
                if feature not in featureStat:
                    featureStat[feature] = {0:0, 1:0}
                featureStat[feature][classLabel] += 1
    return numInstances

In [4]:
featureStat = {}
numPositiveInstances = count(featureStat, "train.positive", 1)
numNegativeInstances = count(featureStat, "train.negative", 0)
print(numPositiveInstances,numNegativeInstances)

797 799


2. Now, compute the conditional probabilities $P(w_i = 1 | C = c)$, i.e. probability of specific feature $w_i$ to be present in a document from class $c$. Use Laplace smooting to avoid zero probabilities.

In [5]:
conditional_probs = {}
for wi in featureStat:
    Prob_0= float(featureStat[wi][0]+1)/float(numNegativeInstances+len(featureStat))
    Prob_1= float(featureStat[wi][1]+1)/float(numPositiveInstances+len(featureStat))
    conditional_probs[wi]={0: Prob_0, 1: Prob_1}

print(conditional_probs)

{'atmosphere': {0: 3.652167561447719e-05, 1: 3.652300949598247e-05}, 'they': {0: 0.0041634710200504, 1: 0.003981008035062089}, 'you__unfamiliar': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, 'distant': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, 'background__of': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, 'the__fictional': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, 'their__struggle': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, 'happiness': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, ',__greedy': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, 'glimpse': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, 'fit': {0: 0.000584346809831635, 1: 0.0007304601899196494}, 'of__unfortunate': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, '.__hover': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, ',__connive': {0: 1.8260837807238595e-05, 1: 3.652300949598247e-05}, 'the__scheme': {0: 1.8260837807238595e-05

In [6]:
print(featureStat['atmosphere'])

{0: 1, 1: 1}


In [7]:
print(conditional_probs['atmosphere'][0])

3.652167561447719e-05


3. Implement a Naive Bayes classfier function that predicts whether a given document belongs to the positive or the negative class. To avoid problems of very small numbers, instead of computing $P(C=c) \cdot \prod_i P(w_i = a_i| C=c)$ cosider computing the $\log$ of that.

In [13]:
import math 

def NaiveBayes(doc):
  log_prob_0 = 0
  log_prob_1 = 0
  length=float(len(featureStat))
  len_log=math.log(length)
  for wi in doc:
    if wi in featureStat:
      Product_0=conditional_probs[wi][0]
      Product_1=conditional_probs[wi][1]
    else:
      Product_0=float(1)/float(numPositiveInstances+len(featureStat))
      Product_1=float(1)/float(numPositiveInstances+len(featureStat))
    log_prob_0 += math.log(Product_0)-len_log
    log_prob_1 += math.log(Product_1)-len_log
  Prob_0 =log_prob_0+math.log(float(numNegativeInstances))-len_log
  Prob_1 =log_prob_1+math.log(float(numPositiveInstances))-len_log
  # print("Probabilistic")
  # print(Prob_0,Prob_1)
  return 0 if Prob_0 > Prob_1 else 1

4. Let's now read the test dataset from the files

In [9]:
def getInstances(fname, classLabel):
    data = []
    with open(fname) as file:
        for line in file:
            data.append((classLabel, line.strip().split()))
    return data

# Read test data
test_data = getInstances("test.positive", 1)
test_data.extend(getInstances("test.negative", 0))

In [10]:
print(test_data)

[(1, ['least__8-10', 'serve__the', 'set', 'an__elegant', 'give__it', 'plate', 'color', 'soup__course', 'elegant__look', 'the__color', 'serveware__for', 'many__of', 'elegant', 'something__not', 'dinnerwares__&amp;', 'something', 'under__plate', 'size__be', 'the__soup', 'a__little', 'find', 'little__overprice', 'size', 'be__something', 'use', 'appear', 'elegant__way', 'it__appear', 'usual__tureen', 'give', 'least', 'be__use', 'overprice', 'color__of', 'of__serve', 'tureen__set', 'serve__its', 'way', 'which__give', 'adequate', 'serveware', 'serve__at', 'dinnerwares', 'which', 'traditional__serveware', 'a__traditional', 'adequate__to', 'serve', 'little', '8-10', 'the__tureen', 'with__many', 'look__but', 'set__which', 'appear__a', 'allow__it', 'not', 'course__the', '&amp;', 'with__usual', 'plate__be', 'use__with', 'find__with', 'the__size', '&amp;__the', 'to__serve', 'look', 'course', 'many', '8-10__people.the', 'be__adequate', 'not__find', 'people.the__under', 'at__least', 'the__dinnerware

4. Evaluate accuracy of the Naive Bayes algorithm on the test data

In [14]:
def NaiveBayes_accuracy(test_data):
  length=len(test_data)
  class_predict = {}
  for (y,doc) in test_data:
    if y not in class_predict:
      class_predict[y] = {0:0, 1:0}
    class_predict[y][NaiveBayes(doc)]+= 1
  # print(class_predict)
  sum_result = class_predict[0][0]+class_predict[1][1]
  # print(sum_result)
  return float(sum_result)/float(length)

print(NaiveBayes_accuracy(test_data))

0.8417085427135679


5. Modify the code and see what happens if we do not use Laplace smoothing